In [166]:
import pandas as pd
import ast
import re


### Import bazy danych przepisów i pliku zawierającego składniki:

In [167]:
data = pd.read_csv("./../data/recipe-dataset.csv")
print(data.head(3))

all_ing = pd.read_csv("../data/all-ingredients.txt", header=None, names=["Ingredient"])


   Unnamed: 0                                              Title  \
0           0  Miso-Butter Roast Chicken With Acorn Squash Pa...   
1           1                    Crispy Salt and Pepper Potatoes   
2           2                        Thanksgiving Mac and Cheese   

                                         Ingredients  \
0  ['1 (3½–4-lb.) whole chicken', '2¾ tsp. kosher...   
1  ['2 large egg whites', '1 pound new potatoes (...   
2  ['1 cup evaporated milk', '1 cup whole milk', ...   

                                        Instructions  \
0  Pat chicken dry with paper towels, season all ...   
1  Preheat oven to 400°F and line a rimmed baking...   
2  Place a rack in middle of oven; preheat to 400...   

                                          Image_Name  \
0  miso-butter-roast-chicken-acorn-squash-panzanella   
1         crispy-salt-and-pepper-potatoes-dan-kluger   
2         thanksgiving-mac-and-cheese-erick-williams   

                                 Cleaned_Ingredients

### Usunięcie zbędnych kolumn, duplikatów i pustych pól:

In [168]:
all_ing = all_ing["Ingredient"].tolist()

data.dropna(inplace=True)
data.drop_duplicates(inplace=True)

columns_to_drop = ["Unnamed: 0", "Ingredients", "Instructions", "Image_Name"]
data.drop(columns=columns_to_drop, inplace=True)
data.rename(columns={"Cleaned_Ingredients": "Ingredients"}, inplace=True)
print(data.head(5))


                                               Title  \
0  Miso-Butter Roast Chicken With Acorn Squash Pa...   
1                    Crispy Salt and Pepper Potatoes   
2                        Thanksgiving Mac and Cheese   
3                 Italian Sausage and Bread Stuffing   
4                                       Newton's Law   

                                         Ingredients  
0  ['1 (3½–4-lb.) whole chicken', '2¾ tsp. kosher...  
1  ['2 large egg whites', '1 pound new potatoes (...  
2  ['1 cup evaporated milk', '1 cup whole milk', ...  
3  ['1 (¾- to 1-pound) round Italian loaf, cut in...  
4  ['1 teaspoon dark brown sugar', '1 teaspoon ho...  


### Dodanie kolumn ze składnikami do zbioru:

In [173]:
# Upewnijmy się, że wszystkie wartości w "Ingredients" są stringami
data["Ingredients"] = data["Ingredients"].apply(lambda x: ' '.join(map(str, x)) if isinstance(x, list) else str(x))

# Teraz sprawdzamy, czy dany składnik występuje w każdym wierszu
for ing in all_ing:
    data[ing] = data["Ingredients"].apply(lambda x: 1 if ing.lower() in str(x).lower() else 0)

print(data.head())



AttributeError: 'float' object has no attribute 'lower'

In [ ]:
# def clean_ingredient_list(ingredients):
#     cleaned = []
#     for ing in ingredients:
#         ing = re.sub(r'[^a-zA-Z ]', '', ing)
#         ing = ing.lower().strip()
#         words_to_remove = ["cup", "cups", "tsp", "tbsp", "pound", "pounds", "ounce", "ounces", "oz", "lb",
#     "teaspoon", "teaspoons", "tablespoon", "tablespoons", "whole", "qt", "g",
#     "to", "package", "packages", "box", "bunch", "can", "cans", "bottle", "bottles",
#     "small", "medium", "large", "fresh", "dried", "divided", "preferably", "for", "serving"]
#         ing = " ".join([word for word in ing.split() if word not in words_to_remove])
#         if ing:
#             cleaned.append(ing)
#     return list(set(cleaned))

# data["Ingredients"] = data["Ingredients"].apply(lambda x: clean_ingredient_list(ast.literal_eval(x)) if isinstance(x, str) else clean_ingredient_list(x))
# data["Ingredients"].head(15)

In [ ]:
# print(data.head(5))
# data.to_csv('../data/clean-ingredients.csv')

Trenowanie modelu na podstawie kolumny **Cleaned_Ingredients** oraz pasującej do składników nazwy danego dania - reszta danych jest zwracana już dla klienta na podstawie odgadnietego tytułu.

Cel modelu: na bazie dostępnych składników klienta (input) model przewiduje jakie dania może zrobić (output: title + id)

wykorzystanie modelu: model zwraca tytuł i ID dania -> potem access już jest po ID do bazy danych aby otrzymać dokładny przepis

In [ ]:
# do modelu nie są potrzebne kolumny: Ingredients, Instructions i Image_Name
# Dataset powinien zawierać: id (do identyfikacji w db, tylko do outputu); Title (docelowy output); <wszystkie kolumny odpowiadające składnikom, z zaznaczeniem 1/0 czy dany przepis je zawiera>
# używamy multilabel classification 
# polecajka n najlepszych przepisow 
# mozna dodac do outputu ilość brakujacych skladnikow (i jakie, ale jeszcze idk jak)

In [ ]:
print(data['Ingredients'].apply(len))

0        830
1        251
2        289
3        558
4        218
        ... 
13496    413
13497    405
13498    271
13499    211
13500    762
Name: Ingredients, Length: 13493, dtype: int64


In [ ]:
for row in data['Ingredients']:
    print(f"Row type: {type(row)}, Content: {row}")

Row type: <class 'list'>, Content: ['dry white wine', 'ground allspice', 'freshly ground pepper', 'kosher salt plus more', 'loaf goodquality sturdy white bread torn into pieces about', 'apple cider vinegar', 'unsalted butter room temperature', 'freshly ground black pepper', 'finely chopped sage', 'apples such as gala or pink lady about total cored cut into pieces', 'chicken', 'unsalted butter melted plus room temperature', 'kosher salt', 'pinch of crushed red pepper flakes', 'extravirgin olive oil', 'allpurpose flour', 'unsalted chicken broth', 'acorn squash about total', 'white miso', 'red onion thinly sliced', 'finely chopped rosemary']
Row type: <class 'list'>, Content: ['kosher salt', 'finely chopped thyme', 'finely chopped rosemary', 'finely chopped parsley', 'new potatoes about inch in diameter', 'egg whites', 'finely ground black pepper']
Row type: <class 'list'>, Content: ['evaporated milk', 'garlic powder', 'extrasharp cheddar coarsely grated', 'milk', 'elbow macaroni', 'fresh

In [ ]:
# data['Ingredients'].map(type).unique()
# unique_ingredients = set(ingredient for row in data['Ingredients'] for ingredient in row)
# ingredient_columns = {}

# for ingredient in unique_ingredients:
#     ingredient_columns[ingredient] = data['Ingredients'].apply(lambda x: 1 if ingredient in x else 0)

# clean_data = pd.concat([data, pd.DataFrame(ingredient_columns)], axis=1)

# print(data.head(5))